<a href="https://colab.research.google.com/github/rd27995/Kaggle_Competition/blob/master/Customer_Pred.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [0]:
#Import the essentials
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import gc
import os
import logging
import datetime
import warnings
import numpy as np
import pandas as pd
import seaborn as sns
from tqdm import tqdm_notebook
import matplotlib.pyplot as plt
from sklearn.metrics import mean_squared_error
from sklearn.decomposition import PCA
from sklearn.metrics import roc_auc_score, roc_curve
from sklearn.model_selection import StratifiedKFold
from sklearn.preprocessing import StandardScaler
import plotly.plotly as py
from sklearn import metrics
from sklearn.preprocessing import StandardScaler
import plotly
plotly.tools.set_credentials_file(username='rahul_rd', api_key='4e1W4nz6b3xxG567gv01')
from IPython.display import display
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LogisticRegression 
pd.options.display.max_rows = None
warnings.filterwarnings('ignore')

In [0]:
##Read the data

data = pd.read_csv('train.csv')


In [6]:
## Get the shape
data.shape

(200000, 202)

In [0]:
##Take a glimpse
data.head()

In [0]:
data.dtypes

In [0]:


data.target.value_counts()

0    179902
1     20098
Name: target, dtype: int64

In [0]:
data = data.loc[:, data.columns != 'ID_code']

In [0]:
X = data.loc[:, data.columns != 'target']


In [0]:
X.head()

In [0]:
y = data.iloc[:,0]

In [0]:
y.head()

In [0]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size = 0.20,random_state=123)

In [0]:
y_train.head()

In [0]:
type(y_train)

pandas.core.series.Series

In [0]:
classifier = LogisticRegression ()


In [0]:
classifier.fit(X_train,y_train)


LogisticRegression(C=1.0, class_weight=None, dual=False, fit_intercept=True,
          intercept_scaling=1, max_iter=100, multi_class='warn',
          n_jobs=None, penalty='l2', random_state=None, solver='warn',
          tol=0.0001, verbose=0, warm_start=False)

In [0]:
y_pred = classifier.predict(X_test)

In [0]:
from sklearn.metrics import confusion_matrix

In [0]:
cm = confusion_matrix(y_test,y_pred)

In [100]:
cm

array([[35826,    89],
       [ 3347,   738]])

In [0]:
fpr, tpr, thresholds = metrics.roc_curve(y_test, y_pred, pos_label=None)


In [0]:
metrics.auc(fpr, tpr)

0.6270294424417541

In [0]:
X_train.describe()

In [0]:
#standard deviation is relatively large for both train and test variable data;
#min, max, sdt values for train and test data looks quite close;
#mean values are distributed over a large range

In [0]:
pca = PCA(n_components=None)

In [0]:
X_train = pca.fit_transform(X_train)

In [0]:
X_test = pca.fit_transform(X_test)

In [0]:
explained_variance = pca.explained_variance_

In [0]:
explained_variance

In [0]:
X_std = StandardScaler().fit_transform(X)

In [0]:
X_std.shape[0]-1

199999

In [0]:
mean_vec = np.mean(X_std, axis=0)
cov_mat = (X_std - mean_vec).T.dot((X_std - mean_vec)) / (X_std.shape[0]-1)
print('Covariance matrix \n%s' %cov_mat)

In [0]:
cov_mat = np.cov(X_std.T)
eig_vals, eig_vecs = np.linalg.eig(cov_mat)

In [0]:
for ev in eig_vecs:
    np.testing.assert_array_almost_equal(1.0, np.linalg.norm(ev))

In [0]:
# Make a list of (eigenvalue, eigenvector) tuples
eig_pairs = [(np.abs(eig_vals[i]), eig_vecs[:,i]) for i in range(len(eig_vals))]

# Sort the (eigenvalue, eigenvector) tuples from high to low
eig_pairs.sort()
eig_pairs.reverse()


# Visually confirm that the list is correctly sorted by decreasing eigenvalues
print('Eigenvalues in descending order:')
n=1
for i in eig_pairs:
    print(n)
    print(i[0])
    n=n+1

In [0]:
tot = sum(eig_vals)
var_exp = [(i / tot)*100 for i in sorted(eig_vals, reverse=True)]
cum_var_exp = np.cumsum(var_exp)

In [0]:
trace1 = dict(
    type='bar',
    x=['PC %s' %i for i in range(1,201)]
    y=var_exp,
    name='Individual'
)

trace2 = dict(
    type='scatter',
    x=['PC %s' %i for i in range(1,201)]
    y=cum_var_exp,
    name='Cumulative'
)


In [4]:
trace1

NameError: ignored

In [0]:
PCA_data = [trace1, trace2]

In [0]:
PCA_data

In [0]:
layout=dict(
    title='Explained variance by different principal components',
    yaxis=dict(
        title='Explained variance in percent'
    ),
    annotations=list([
        dict(
            x=1.16,
            y=1.05,
            xref='paper',
            yref='paper',
            text='Explained Variance',
            showarrow=False,
        )
    ])
)

fig = dict(data=PCA_data, layout=layout)


In [0]:
py.iplot(fig)

In [0]:
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot

In [0]:
sc = StandardScaler()

In [0]:
X_train1 = sc.fit_transform(X_train)
X_test1 = sc.transform(X_test)

In [0]:
import lightgbm as lgb

In [0]:
d_train = lgb.Dataset(X_train1,y_train)

In [0]:
## Best Iteration

In [0]:
params = {}
params['learning_rate'] = 0.01
params['boosting_type'] = 'gbdt'
params['objective'] = 'binary'
params['metric'] = 'binary_error'
params['n_thread'] = 13
params['num_leaves'] = 32
params['bagging_fraction'] = 0.75
params['feature_fraction'] = 0.041
params['subsample_for_bin'] = 200
params['bagging_freq'] = 1
params['colsample_bytree'] = 0.7
params['reg_alpha'] = 1
params['reg_lambda'] = 2
params['min_split_gain'] = 0.5
params['min_child_weight'] = 1
params['min_child_samples'] = 5
params['scale_pause_weight'] = 1
params['max_depth'] = -1
params['min_data_in_leaf'] = 1500
clf = lgb.train(params, d_train, 8000)

In [0]:
#Prediction
y_pred=clf.predict(X_test1)

       


In [117]:
fpr, tpr, thresholds = metrics.roc_curve(y_test, y_pred, pos_label=None)
metrics.auc(fpr,tpr)

0.8982721170668335

In [118]:
cm = confusion_matrix(y_test,y_pred)

ValueError: ignored

In [113]:
cm


array([[35578,   337],
       [ 2783,  1302]])

In [92]:
y_pred_new.dtype

dtype('int64')

In [0]:
y_pred_new = y_pred.astype(int)
    

In [0]:
customers = pd.read_csv('test.csv')

In [22]:
customers.shape

(200000, 201)

In [0]:
customers_w = customers.loc[:, customers.columns != 'ID_code']

In [0]:
customers_w.head()

var_0    var_1    var_2   var_3    var_4   var_5   var_6    var_7  \
0  11.0656   7.7798  12.9536  9.4292  11.4327 -2.3805  5.8493  18.2675   
1   8.5304   1.2543  11.3047  5.1858   9.1974 -4.0117  6.0196  18.6316   
2   5.4827 -10.3581  10.1407  7.0479  10.2628  9.8052  4.8950  20.2537   
3   8.5374  -1.3222  12.0220  6.5749   8.8458  3.1744  4.9397  20.5660   
4  11.7058  -0.1327  14.1295  7.7506   9.1035 -8.5848  6.8595  10.6048   

    var_8   var_9   ...     var_190  var_191  var_192  var_193  var_194  \
0  2.1337  8.8100   ...     -2.1556  11.8495  -1.4300   2.4508  13.7112   
1 -4.4131  5.9739   ...     10.6165   8.8349   0.9403  10.1282  15.5765   
2  1.5233  8.3442   ...     -0.7484  10.9935   1.9803   2.1800  12.9813   
3  3.3755  7.4578   ...      9.5702   9.0766   1.6580   3.5813  15.1874   
4  2.9890  7.1437   ...      4.2259   9.1723   1.2835   3.3778  19.5542   

   var_195  var_196  var_197  var_198  var_199  
0   2.4669   4.3654  10.7200  15.4722  -8.7197  
1   0.4773  -1.4852   9.8714  19.1293 -20.9760  
2   2.1281  -7.1086   7.0618  19.8956 -23.1794  
3   3.1656   3.9567   9.2295  13.0168  -4.2108  
4  -0.2860  -5.1612   7.2882  13.9260  -9.1846  

[5 rows x 200 columns]

In [0]:
#Submission Prediction
y_pred=clf.predict(customers_w)


In [0]:
y_pred.dtype

dtype('float64')

In [120]:
len(y_pred)

200000

In [0]:
sub_df = pd.DataFrame({"ID_code": customers["ID_code"].values})

In [0]:
sub_df['Target'] = y_pred

In [123]:
sub_df.tail(n=50)

ID_code    Target
199950  test_199950  0.998261
199951  test_199951  0.999210
199952  test_199952  0.999050
199953  test_199953  0.999044
199954  test_199954  0.999168
199955  test_199955  0.994512
199956  test_199956  0.999361
199957  test_199957  0.999625
199958  test_199958  0.998973
199959  test_199959  0.998725
199960  test_199960  0.998799
199961  test_199961  0.999188
199962  test_199962  0.999716
199963  test_199963  0.999756
199964  test_199964  0.999606
199965  test_199965  0.998277
199966  test_199966  0.998894
199967  test_199967  0.996673
199968  test_199968  0.999585
199969  test_199969  0.999494
199970  test_199970  0.999306
199971  test_199971  0.998824
199972  test_199972  0.999017
199973  test_199973  0.998859
199974  test_199974  0.993438
199975  test_199975  0.999401
199976  test_199976  0.999825
199977  test_199977  0.999836
199978  test_199978  0.999103
199979  test_199979  0.999124
199980  test_199980  0.999296
199981  test_199981  0.999463
199982  test_199982  0.999399
199983  test_199983  0.999500
199984  test_199984  0.998149
199985  test_199985  0.999542
199986  test_199986  0.999598
199987  test_199987  0.998897
199988  test_199988  0.998945
199989  test_199989  0.996152
199990  test_199990  0.997924
199991  test_199991  0.998823
199992  test_199992  0.999407
199993  test_199993  0.999475
199994  test_199994  0.999801
199995  test_199995  0.999254
199996  test_199996  0.999253
199997  test_199997  0.996519
199998  test_199998  0.999439
199999  test_199999  0.999196

In [0]:
## To check the values in the outcome of test data

sub2_df = pd.DataFrame({"Check":y_pred})


In [26]:
sub2_df.Check.value_counts()

0.866525    1
0.943614    1
0.906646    1
0.831951    1
0.887337    1
0.866339    1
0.896997    1
0.825856    1
0.865600    1
0.847213    1
0.918276    1
0.944569    1
0.893146    1
0.885454    1
0.932814    1
0.861213    1
0.921351    1
0.912479    1
0.865104    1
0.900206    1
0.791622    1
0.854762    1
0.920852    1
0.886095    1
0.765015    1
0.822693    1
0.933408    1
0.862073    1
0.969787    1
0.816058    1
0.939684    1
0.937274    1
0.893011    1
0.871269    1
0.846308    1
0.885775    1
0.893750    1
0.911509    1
0.901084    1
0.844598    1
0.829234    1
0.716704    1
0.829218    1
0.915167    1
0.913527    1
0.889391    1
0.857625    1
0.871110    1
0.901214    1
0.914947    1
0.830898    1
0.882538    1
0.728239    1
0.825827    1
0.850881    1
0.841578    1
0.901852    1
0.854337    1
0.864525    1
0.881736    1
0.756638    1
0.943143    1
0.944562    1
0.889614    1
0.936327    1
0.929037    1
0.882511    1
0.938338    1
0.906486    1
0.775104    1
0.928019    1
0.8606

In [124]:
y_pred.min()

0.9384447784498943

In [0]:
## Excel

sub_df.to_csv('Submission_7',sep = ',')

In [0]:
#convert into binary values
y_pred1 = y_pred
for i in range(0,len(X_test)):
    if y_pred[i]>=.5:      
       y_pred1[i]=1
       
    else:  
       y_pred1[i]=0

In [0]:
model = lgb.LGBMClassifier(objective = "binary", 
    learning_rate = 0.01,
    boosting_type = "gbdt",
    metric = "binary_error",
    n_thread = 13,
    num_leaves = 32,                          
    bagging_fraction = 0.75, 
    feature_fraction = 0.041,
    subsample_for_bin = 200,
    bagging_freq = 1,
    colsample_bytree = 0.7,
    reg_alpha = 1,
    reg_lambda = 2,
    min_split_gain = 0.5,
    min_child_weight = 1,
    min_child_samples = 5,
    scale_pause_weight = 1,
    max_depth = -1,
    min_data_in_leaf = 1500,
    num_iterations =99999999,
    seed=44000)
    


In [134]:
model.fit(X_train1, y_train, 
              eval_set=[(X_test1, y_test)],
              verbose=3500, 
              early_stopping_rounds=3500)
                  
cv_val = model.predict_proba(X_test1)[:,1]
    
    #Save LightGBM Model
save_to = '{}{}_fold{}.txt'.format(lgb_path, name, counter+1)
model.booster_.save_model(save_to)
    
    

Training until validation scores don't improve for 3500 rounds.
[3500]	valid_0's binary_error: 0.083925
[7000]	valid_0's binary_error: 0.077875
[10500]	valid_0's binary_error: 0.07695


KeyboardInterrupt: ignored

In [130]:
fit_lgb(X_train1, y_train, X_test1, y_test, counter, lgb_path, name)

NameError: ignored